In [1]:
# Copyright 2024 Keysight Technologies Inc.

In [2]:
import keysight.qcs as qcs
import numpy as np

n_targets = 4
qubits = qcs.Qudits(range(n_targets))
drive_channels = qcs.Channels(range(n_targets), "xy_channels")

In [3]:
zxz = qcs.ParametricGate(
    [-qcs.PAULIS.sigma_z, qcs.PAULIS.sigma_x, qcs.PAULIS.sigma_z],
    ["phi", "theta", "phi"],
)
phis = qcs.Array(name="phis", shape=len(qubits), dtype=float)
thetas = qcs.Array(name="thetas", shape=len(qubits), dtype=float)
zxz_param_gate = qcs.ParameterizedGate(zxz, [phis, thetas])

In [4]:
freq_values = [5e9 + 100e6 * n for n in range(n_targets)]
frequency_cals = qcs.Array("single_qubit_frequencies", value=freq_values, dtype=float)
amplitude_cals = qcs.Array("single_qubit_amplitudes", value=[0.5] * n_targets)
pulse_duration = qcs.Scalar("single_qubit_duration", value=30e-9, dtype=float)

In [5]:
replacement_program = qcs.Program()

# each channel can have an independent amplitude, encoded as
# the product of the intended angle of rotation and the calibrated amplitude scale

envelope = qcs.GaussianEnvelope()
# waveform phases are equal to intended axis of rotation
waveforms = qcs.RFWaveform(
    pulse_duration,
    envelope,
    amplitude_cals * thetas,
    rf_frequency=frequency_cals,
    instantaneous_phase=phis,
)

# add the waveforms to all channels
node = replacement_program.add_waveform(waveforms, drive_channels)

In [6]:
linker = qcs.ParameterizedLinker(zxz_param_gate, qubits, replacement_program)

In [7]:
program = qcs.Program()

some_qubits = qcs.Qudits([0, 2, 3])
some_thetas = qcs.Array("some_thetas", value=[np.pi / 2, np.pi / 3, np.pi / 4])
some_phis = qcs.Array("some_phis", value=[0.0, 0.0, np.pi / 2])
program.add_parametric_gate(zxz, [some_phis, some_thetas], some_qubits)

linker_pass = qcs.LinkerPass(linker)
program_compiled = linker_pass.apply(program)

In [8]:
program_compiled.render(
    channel_subplots=False,
    lo_frequency=5e9,
    sample_rate=qcs.SAMPLE_RATES[qcs.InstrumentEnum.M5300AWG],
)

In [9]:
linker.program.variables.single_qubit_frequencies[0].value += 50e6
linker.program.variables.single_qubit_amplitudes[2].value *= 0.5

program_compiled.render(
    channel_subplots=False,
    lo_frequency=5e9,
    sample_rate=qcs.SAMPLE_RATES[qcs.InstrumentEnum.M5300AWG],
)